In [1]:
import pandas as pd
from tqdm import tqdm # Fortschrittsanzeige für pandas
tqdm.pandas()
tweet_csv = '../data/copbird_table_tweet.csv'
entity_csv =  '../data/copbird_table_entity.csv'
user_csv = '../data/copbird_table_user.csv'
geo_csv = '../geolocations/polizei_accounts_geo.csv'

limit = None
tweets = pd.read_csv(tweet_csv, nrows=limit)
entities = pd.read_csv(entity_csv, nrows=limit)
users = pd.read_csv(user_csv, nrows=limit)
geo = pd.read_csv(geo_csv, nrows=limit, sep="\t")

In [2]:
#tweets["contains"] = tweets["tweet_text"].str.contains(r'(([@])\w)')
#tweets_subset = tweets[tweets["contains"]]
#tweets_subset["mention"] = tweets_subset["tweet_text"].str.extract(r'(([@])\w)')
mentions = entities[entities["entity_type"]=="mention"]

In [3]:
mentions.head(10)

tweet_id             tag entity_type
0  1321021123463663616      mahanna196     mention
1  1321025127388188673             bka     mention
2  1321028108665950208  StrupeitVolker     mention
3  1321029199998656513             bka     mention
4  1321032307277443072      Sitewinder     mention
5  1321033945467834368     GunstickULM     mention
6  1321034866377543680     Korbi161224     mention
7  1321035908146233344     GunstickULM     mention
8  1321036834579894272    retikulum383     mention
9  1321036834579894272      FPolitiker     mention

In [4]:
tweets_stripped = tweets[["id", "user_id"]]
tweets_stripped.head(5)

id             user_id
0  1321021123463663616  778895426007203840
1  1321023114071969792          2397974054
2  1321025127388188673          2397974054
3  1321028108665950208          2810902381
4  1321029199998656513           223758384

In [5]:
mentions_inter = mentions.merge(tweets_stripped, left_on="tweet_id", right_on="id")
mentions_inter2 = mentions_inter.merge(users, left_on="user_id", right_on="id")
merged = mentions_inter2[["tweet_id", "user_id", "handle", "tag"]]
merged["connection"] = merged["handle"]+ "->"+ merged["tag"]


<ipython-input-5-d55278231e86>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  merged["connection"] = merged["handle"]+ "->"+ merged["tag"]


In [6]:
merged2 = merged.groupby('connection').size().reset_index(name='count').sort_values(by='count', ascending=False)
merged2.size

23796

In [7]:
merged.head(5)

tweet_id             user_id      handle              tag  \
0  1321021123463663616  778895426007203840  Polizei_OL       mahanna196   
1  1321037834246066181  778895426007203840  Polizei_OL       mahanna196   
2  1321073940199100416  778895426007203840  Polizei_OL     Emma36166433   
3  1321096827937185793  778895426007203840  Polizei_OL         line9600   
4  1321338058600570880  778895426007203840  Polizei_OL  Keroth_Katlatas   

                    connection  
0       Polizei_OL->mahanna196  
1       Polizei_OL->mahanna196  
2     Polizei_OL->Emma36166433  
3         Polizei_OL->line9600  
4  Polizei_OL->Keroth_Katlatas

connection count ist mit "duplicates" weil mit tweet_ids, cc_wo_id (connection count without id) ist darum bereingt

In [8]:
connection_count = pd.merge(merged2, merged, how="left", on="connection")
cc_wo_id = connection_count[["connection", "count", "user_id", "handle", "tag"]]
cc_wo_id = cc_wo_id.drop_duplicates()

In [9]:
from pyvis.network import Network

data = cc_wo_id.head(15000)

cop_net = Network(height='500px', width='100%', bgcolor='#222222', font_color='white', notebook=True)

cop_net.barnes_hut()

sources = data['handle']
targets = data['tag']
weights = data['count']

edge_data = zip(sources, targets, weights)

for e in edge_data:
    src = e[0]
    dst = e[1]
    w = e[2]

    cop_net.add_node(src, src, title=src)
    cop_net.add_node(dst, dst, title=dst)
    cop_net.add_edge(src, dst, value=w)

neighbor_map = cop_net.get_adj_list()

# add neighbor data to node hover data
for node in cop_net.nodes:
    node['title'] += ' Neighbors:<br>' + '<br>'.join(neighbor_map[node['id']])
    node['value'] = len(neighbor_map[node['id']])

#cop_net.show('copnet.html')

KeyboardInterrupt: 

In [10]:
cc_wo_id.head(10)

connection  count             user_id          handle  \
0           Polizei_Ffm->Stadt_FFM    137          2272909014     Polizei_Ffm   
137  polizei_nrw_me->KreisMettmann    132          2389359068  polizei_nrw_me   
269       Polizei_OHA->Polizei_GOE     82  773805850687340544     Polizei_OHA   
351             LkaBaWue->LkaBaWue     78  814455464394182656        LkaBaWue   
429   Polizei_nrw_ms->Feuerwehr_MS     69          2284811875  Polizei_nrw_ms   
498            Polizei_KA->Natenom     65          3029998264      Polizei_KA   
563       Polizei_KA->axel_gutmann     61          3029998264      Polizei_KA   
624  polizei_nrw_do->stadtdortmund     61           769128278  polizei_nrw_do   
685    Polizei_nrw_ms->muenster_de     59          2284811875  Polizei_nrw_ms   
744      polizei_nrw_bo->FW_Bochum     57          2389155192  polizei_nrw_bo   

               tag  
0        Stadt_FFM  
137  KreisMettmann  
269    Polizei_GOE  
351       LkaBaWue  
429   Feuerwehr_MS  
498        Natenom  
563   axel_gutmann  
624  stadtdortmund  
685    muenster_de  
744      FW_Bochum

In [11]:
geo_neu = geo[["Polizei Account", "LAT", "LONG"]]
geo_neu2 = geo[["Polizei Account", "LAT", "LONG"]]

In [12]:
geo_neu.head(1)

Polizei Account LAT LONG
0        bpol_11    -  NaN

In [13]:
cc_wo_id['handle'] = cc_wo_id['handle'].str.lower()
cc_wo_id['handle'] = cc_wo_id['handle'].str.strip()
cc_wo_id['tag'] = cc_wo_id['tag'].str.lower()
cc_wo_id['tag'] = cc_wo_id['tag'].str.strip()
geo_neu['Polizei Account'] = geo_neu['Polizei Account'].str.lower()
geo_neu['Polizei Account'] = geo_neu['Polizei Account'].str.strip()
merged_geo = pd.merge(cc_wo_id, geo_neu, how="left", left_on="handle", right_on="Polizei Account")
merged_geo = merged_geo.rename(columns={"LAT": "LAT1", "LONG": "LONG1"})


<ipython-input-13-9989204024e1>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  geo_neu['Polizei Account'] = geo_neu['Polizei Account'].str.lower()
<ipython-input-13-9989204024e1>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  geo_neu['Polizei Account'] = geo_neu['Polizei Account'].str.strip()


In [14]:
merged_geo.head(5)

connection  count             user_id          handle  \
0         Polizei_Ffm->Stadt_FFM    137          2272909014     polizei_ffm   
1  polizei_nrw_me->KreisMettmann    132          2389359068  polizei_nrw_me   
2       Polizei_OHA->Polizei_GOE     82  773805850687340544     polizei_oha   
3             LkaBaWue->LkaBaWue     78  814455464394182656        lkabawue   
4   Polizei_nrw_ms->Feuerwehr_MS     69          2284811875  polizei_nrw_ms   

             tag Polizei Account        LAT1       LONG1  
0      stadt_ffm     polizei_ffm   50.110922    8.682127  
1  kreismettmann  polizei_nrw_me  51.2527778   6.9777778  
2    polizei_goe     polizei_oha    51.72784  10.2508204  
3       lkabawue        lkabawue   48.775846    9.182932  
4   feuerwehr_ms  polizei_nrw_ms  51.9625101   7.6251879

In [15]:
merged_geo2 = pd.merge(merged_geo, geo_neu, how="left", left_on="tag", right_on="Polizei Account")
merged_geo2 = merged_geo2.rename(columns={"LAT": "LAT2", "LONG": "LONG2"})

In [16]:
merged_geo2.head(5)

connection  count             user_id          handle  \
0         Polizei_Ffm->Stadt_FFM    137          2272909014     polizei_ffm   
1  polizei_nrw_me->KreisMettmann    132          2389359068  polizei_nrw_me   
2       Polizei_OHA->Polizei_GOE     82  773805850687340544     polizei_oha   
3             LkaBaWue->LkaBaWue     78  814455464394182656        lkabawue   
4   Polizei_nrw_ms->Feuerwehr_MS     69          2284811875  polizei_nrw_ms   

             tag Polizei Account_x        LAT1       LONG1 Polizei Account_y  \
0      stadt_ffm       polizei_ffm   50.110922    8.682127               NaN   
1  kreismettmann    polizei_nrw_me  51.2527778   6.9777778               NaN   
2    polizei_goe       polizei_oha    51.72784  10.2508204       polizei_goe   
3       lkabawue          lkabawue   48.775846    9.182932          lkabawue   
4   feuerwehr_ms    polizei_nrw_ms  51.9625101   7.6251879               NaN   

        LAT2     LONG2  
0        NaN       NaN  
1        NaN       NaN  
2  51.541280  9.915804  
3  48.775846  9.182932  
4        NaN       NaN

In [17]:
geo_stripped = merged_geo2[["LAT1", "LONG1", "LAT2", "LONG2", "count"]]
geo_stripped = geo_stripped.dropna()
geo_stripped = geo_stripped[geo_stripped.LAT1 != "-"]
geo_stripped = geo_stripped[geo_stripped.LAT2 != "-"]
geo_stripped.head(5)

LAT1       LONG1        LAT2       LONG2  count
2     51.72784  10.2508204   51.541280    9.915804     82
3    48.775846    9.182932   48.775846    9.182932     78
22  48.3974003   9.9934336   48.775846    9.182932     36
23   52.120533   11.627624  51.0493286  13.7381437     35
24  52.1315889  11.6399609  52.6050782  11.8594279     34

In [18]:
geo_stripped.dtypes

LAT1     object
LONG1    object
LAT2     object
LONG2    object
count     int64
dtype: object

In [19]:
geo_stripped["LAT1"] = geo_stripped["LAT1"].astype(float)
geo_stripped["LONG1"] = geo_stripped["LONG1"].astype(float)
geo_stripped["LAT2"] = geo_stripped["LAT2"].astype(float)
geo_stripped["LONG2"] = geo_stripped["LONG2"].astype(float)
geo_stripped["count"] = geo_stripped["count"].astype(int)

In [20]:
geo_stripped = geo_stripped.reset_index()

In [21]:
import folium

point = []


for i in geo_stripped.index:
    point.append(([geo_stripped["LAT1"][i], geo_stripped["LONG1"][i]], 
                  [geo_stripped["LAT2"][i], geo_stripped["LONG2"][i]]))
    

In [22]:
#ave_lat = sum(p[0] for p in point)/len(point)
#ave_lon = sum(p[1] for p in point)/len(point)

In [81]:
# Load map centred on average coordinates


In [82]:
geo_stripped.head(5)

index       LAT1      LONG1       LAT2      LONG2  count
0      2  51.727840  10.250820  51.541280   9.915804     82
1      3  48.775846   9.182932  48.775846   9.182932     78
2     22  48.397400   9.993434  48.775846   9.182932     36
3     23  52.120533  11.627624  51.049329  13.738144     35
4     24  52.131589  11.639961  52.605078  11.859428     34

In [83]:
thickness = geo_stripped["count"][0]

In [96]:
geo_handle_pre = geo[["Polizei Account", "Name", "LAT", "LONG"]]
geo_handle_pre = geo_handle_pre.dropna()
geo_handle = geo_handle_pre[geo_handle_pre.LAT != "-"]
geo_handle["LAT"] = geo_handle["LAT"].astype(float)
geo_handle["LONG"] = geo_handle["LONG"].astype(float)
geo_handle = geo_handle.reset_index()

<ipython-input-96-365be8339e30>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  geo_handle["LAT"] = geo_handle["LAT"].astype(float)
<ipython-input-96-365be8339e30>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  geo_handle["LONG"] = geo_handle["LONG"].astype(float)


In [99]:
import colorsys
import branca
import branca.colormap as cm

my_map = folium.Map(location=[geo_stripped["LAT1"][0], geo_stripped["LONG1"][0],], zoom_start=8)

i = 0
for i in geo_handle.index:
    text = geo_handle["Name"].iloc[i]
    name_lat  = geo_handle["LAT"].iloc[i]
    name_long  = geo_handle["LONG"].iloc[i]
    #print(i)
    folium.map.Marker(
        [name_lat, name_long],
        icon=folium.DivIcon(icon_size=(20,10),
        icon_anchor=(0,0), html='<div style="font-size: 12pt">%s</div>'%text)).add_to(my_map)

colormap = cm.LinearColormap(colors=['lightblue', 'orange', 'red'], index=[0,5,60],vmin=0,vmax=90)
i = 0
for j in point:
    thickness = int(geo_stripped["count"][i])
    #folium.PolyLine(j, color=rgb, weight=thickness, opacity=1).add_to(my_map)
    folium.PolyLine(j, color=colormap(thickness), weight=thickness, opacity=0.8).add_to(my_map)
    i = i+1



In [100]:
# Save map
my_map.save("./connections_with_name.html")

In [101]:
my_map_ohne = folium.Map(location=[geo_stripped["LAT1"][0], geo_stripped["LONG1"][0],], zoom_start=8)

colormap = cm.LinearColormap(colors=['lightblue', 'orange', 'red'], index=[0,5,60],vmin=0,vmax=90)
i = 0
for j in point:
    thickness = int(geo_stripped["count"][i])
    #folium.PolyLine(j, color=rgb, weight=thickness, opacity=1).add_to(my_map)
    folium.PolyLine(j, color=colormap(thickness), weight=thickness, opacity=0.8).add_to(my_map_ohne)
    i = i+1


In [102]:
# Save map
my_map_ohne.save("./connections_without_name.html")